# Install Car Dealership Stored Procedures

In [ ]:
from DATA225utils import make_connection

In [ ]:
conn = make_connection(config_file = 'CarDealership.ini')
cursor = conn.cursor()

### **1.a** What sales did each salesperson make during a given month?

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS sales_of_month')

cursor.execute( 
    """
    CREATE PROCEDURE sales_of_month(IN month INT)
    BEGIN
        SELECT sp.name AS spname, 
               car.make, car.model, 
               c.name AS cname, c.gender AS cgender, car.price
        FROM salesperson sp, transaction t, car, customer c
        WHERE t.salesperson_id = sp.id
        AND   t.id = car.transaction_id
        AND   t.customer_id = c.id
        AND   t.month = month
        ORDER BY spname, car.make, car.model, cgender;
    END
    """
)

### **1.b** How many sales did each salesperson make during a given month?

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS sales_counts_of_month')

cursor.execute( 
    """
    CREATE PROCEDURE sales_counts_of_month(IN month INT)
    BEGIN
        SELECT sp.name AS spname, count(sp.name) AS cars_sold
        FROM salesperson sp, transaction t, car, customer c
        WHERE t.salesperson_id = sp.id
        AND   t.id = car.transaction_id
        AND   t.customer_id = c.id
        AND   t.month = month
        GROUP BY spname
        ORDER BY spname;
    END
    """
)

### **1.c** What is the highest number of sales by a salesperson during a given month?
#### Return the number via the `OUT highest INT` parameter.

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS highest_sales_of_month')

cursor.execute( 
    """
    CREATE PROCEDURE highest_sales_of_month(IN month INT, 
                                            OUT highest INT)
    BEGIN
        SELECT count(sp.name) INTO highest
        FROM salesperson sp, transaction t
        WHERE t.salesperson_id = sp.id
        AND   t.month = month
        GROUP BY sp.name
        ORDER BY count(sp.name) DESC
        LIMIT 1;
    END
    """
)

### **1.c** Who are the salesperson(s) of a given month (those who make the highest sales)?

In [ ]:
cursor.execute('DROP PROCEDURE IF EXISTS salespersons_of_the_month')

cursor.execute( 
    """
    CREATE PROCEDURE salespersons_of_the_month(IN month INT)
    BEGIN
        CALL highest_sales_of_month(month, @highest_sales);
    
        SELECT sp.name AS spname, count(sp.name) AS cars_sold 
        FROM salesperson sp, transaction t
        WHERE t.salesperson_id = sp.id
        AND   t.month = month
        GROUP BY spname
        HAVING cars_sold = @highest_sales
        ORDER BY spname;
    END
    """
)

In [ ]:
cursor.close()
conn.close()